In [3]:
import numpy  as np
import pandas as pd
import warnings
warnings.filterwarnings('ignore')
import plotly.express as px
import matplotlib.pyplot as plt

In [20]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.feature_extraction.text import CountVectorizer

In [6]:
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)

In [29]:
call_reason_merged = pd.read_csv('calls_reason.csv')
call = pd.read_csv('callsf0d4f5a.csv')
reason = pd.read_csv('reason18315ff.csv')

In [166]:
cleaned_data_100 = pd.read_csv('merged_table_100_good.csv')

In [37]:
cleaned_data_200 = pd.read_csv('merged_table_200.csv')
cleaned_data_300 = pd.read_csv('merged_table_300.csv')

In [167]:
cleaned_data_100.head()

Unnamed: 0     call_id  customer_id  agent_id  \
0           0  3817230689    390235425    922729   
1           1  4886165173   9360139623    964561   
2           2  9310693795   4367883724    758927   
3           3  4963458977   5621041498    274746   
4           4  4458776244   5335489097    878048   

                                     call_transcript  call_start_datetime  \
0  clair clair seattl thursday johnson ua1572 10a...  2024-08-01 05:03:00   
1  steve suppos 3 miss connect sorri hear never f...  2024-08-01 05:26:00   
2  adam complain suppos morn miss someth import s...  2024-08-01 05:52:00   
3  sarah sarah york 3 miss connect sorri hear tic...  2024-08-01 06:04:00   
4  steve suppos morn miss import sorri hear sir k...  2024-08-01 06:00:00   

  agent_assigned_datetime    call_end_datetime primary_call_reason  
0     2024-08-01 05:12:00  2024-08-01 05:25:00         Post Flight  
1     2024-08-01 05:36:00  2024-08-01 06:20:00         Post Flight  
2     2024-08-01 06:02:00  2024-08-01 06:06:00             Seating  
3     2024-08-01 06:08:00  2024-08-01 06:11:00      Communications  
4     2024-08-01 06:09:00  2024-08-01 06:24:00             Seating

In [168]:
vectorizer = TfidfVectorizer(max_features=1000)  # Limit to top 1000 features if needed
X = vectorizer.fit_transform(cleaned_data_100['call_transcript'])


In [124]:
vectorizer = TfidfVectorizer(max_features=1000)  # Limit to top 1000 features if needed
X = vectorizer.fit_transform(call_reason_merged['call_transcript'])


In [171]:
split_dataframes={}
for i  in cleaned_data_100['primary_call_reason']:
    split_dataframes[i] = cleaned_data_100[cleaned_data_100['primary_call_reason']==i]
    print(i)

Post Flight
Post Flight
Seating
Communications
Seating
Traveler Updates
Communications
Upgrade
IRROPS
Seating
IRROPS
IRROPS
Products and Services
Mileage Plus
nan
Mileage Plus
Seating
IRROPS
Voluntary Change
Booking
nan
IRROPS
IRROPS
Voluntary Change
Post Flight
IRROPS
nan
Seating
Seating
Voluntary Change
Traveler Updates
Digital Support
nan
Seating
Post Flight
Products and Services
Post Flight
Products and Services
Digital Support
nan
IRROPS
Seating
Traveler Updates
IRROPS
IRROPS
Communications
nan
Upgrade
Disability
Voluntary Change
IRROPS
Mileage Plus
Post Flight
Voluntary Cancel
Booking
Booking
IRROPS
Upgrade
Digital Support
Voluntary Change
Baggage
Seating
Post Flight
ETC
Seating
Seating
IRROPS
Mileage Plus
IRROPS
Voluntary Change
Voluntary Cancel
IRROPS
IRROPS
IRROPS
nan
Other Topics
Post Flight
Check In
IRROPS
Baggage
Voluntary Change
IRROPS
Seating
Baggage
Post Flight
Voluntary Change
Products and Services
Post Flight
nan
Schedule Change
ETC
Upgrade
nan
Products and Services
Di

In [183]:
# split_dataframes_uncleaned={}
# for i in call_reason_merged['primary_call_reason']:
#     split_dataframes_uncleaned[i] = call_reason_merged[call_reason_merged['primary_call_reason']==i]
#     print(i)

In [190]:
def apply_lda_to_dataframe(df, n_topics=4, n_top_words=10):
    
    # Step 1: Vectorize the text data using CountVectorizer
    vectorizer = CountVectorizer(max_df=0.95, min_df=2, stop_words='english')
    doc_term_matrix = vectorizer.fit_transform(df['call_transcript'])
    
    # Step 2: Apply LDA
    lda_model = LatentDirichletAllocation(n_components=n_topics, random_state=42)
    lda_model.fit(doc_term_matrix)
    
    # Step 3: Extract the top words for each topic
    words = vectorizer.get_feature_names()  
    
    topic_keywords = []
    for topic_idx, topic in enumerate(lda_model.components_):
        top_words = [words[i] for i in topic.argsort()[:-n_top_words - 1:-1]]  # Top `n_top_words`
        topic_keywords.append(top_words)
    
    # Step 4: Get the topic distribution for each document
    topic_distribution = lda_model.transform(doc_term_matrix)
    
    return lda_model, topic_keywords, topic_distribution

In [191]:
lda_models = {}
topic_keywords = {}
topic_distributions = {}

# Number of topics you want to find per call reason
n_topics_per_reason = 4

# Apply LDA to each split DataFrame
for reason, df in split_dataframes.items():
    if not df.empty:  # Check if the DataFrame is not empty
        print(f"Applying LDA for reason: {reason}")
        lda_model, keywords, distribution = apply_lda_to_dataframe(df, n_topics=n_topics_per_reason)
        
        # Store the LDA model, topic keywords, and topic distribution for each reason
        lda_models[reason] = lda_model
        topic_keywords[reason] = keywords
        topic_distributions[reason] = distribution

        # Assign topic distribution and dominant topic to each transcript in the DataFrame
        df['topic_distribution'] = list(distribution)
        df['dominant_topic'] = distribution.argmax(axis=1)

        # Save the updated DataFrame back
        split_dataframes[reason] = df


Applying LDA for reason: Post Flight
Applying LDA for reason: Seating
Applying LDA for reason: Communications
Applying LDA for reason: Traveler Updates
Applying LDA for reason: Upgrade
Applying LDA for reason: IRROPS
Applying LDA for reason: Products and Services
Applying LDA for reason: Mileage Plus
Applying LDA for reason: Voluntary Change
Applying LDA for reason: Booking
Applying LDA for reason: Digital Support
Applying LDA for reason: Disability
Applying LDA for reason: Voluntary Cancel
Applying LDA for reason: Baggage
Applying LDA for reason: ETC
Applying LDA for reason: Other Topics
Applying LDA for reason: Check In
Applying LDA for reason: Schedule Change
Applying LDA for reason: Checkout
Applying LDA for reason: Unaccompanied Minor


In [192]:
# lda_models_uncleaned = {}
# topic_keywords_uncleaned = {}
# topic_distributions_uncleaned = {}

# # Number of topics you want to find per call reason
# n_topics_per_reason = 4

# # Apply LDA to each split DataFrame
# for reason, df in split_dataframes_uncleaned.items():
#     if not df.empty:  # Check if the DataFrame is not empty
#         print(f"Applying LDA for reason: {reason}")
#         lda_model_uncleaned, keywords_uncleaned, distribution_uncleaned = apply_lda_to_dataframe(df, n_topics=n_topics_per_reason)
        
#         # Store the LDA model, topic keywords, and topic distribution for each reason
#         lda_models_uncleaned[reason] = lda_model_uncleaned
#         topic_keywords_uncleaned[reason] = keywords_uncleaned
#         topic_distributions_uncleaned[reason] = distribution_uncleaned

#         # Assign topic distribution and dominant topic to each transcript in the DataFrame
#         df['topic_distribution'] = list(distribution_uncleaned)
#         df['dominant_topic'] = distribution_uncleaned.argmax(axis=1)

#         # Save the updated DataFrame back
#         split_dataframes_uncleaned[reason] = df


In [184]:
# Display the topics for each reason
for reason, topics in topic_keywords.items():
    print(f"\nCall Reason: {reason}")
    for idx, topic in enumerate(topics):
        print(f"  Topic {idx + 1}: {', '.join(topic)}")

        


Call Reason: Post Flight
  Topic 1: voucher, weather, experi, provid, miss, bag, refund, compens, apolog, happen
  Topic 2: tomorrow, sir, apolog, ugh, connect, guess, inconveni, suppos, sigh, york
  Topic 3: credit, refund, ticket, abl, use, offer, 200, someth, feel, pay
  Topic 4: great, monday, return, tuesday, thursday, friday, email, 150, enjoy, safe

Call Reason: Seating
  Topic 1: 150, monday, great, friday, differ, waiv, tuesday, john, thursday, saturday
  Topic 2: upgrad, bag, doubl, question, economi, everyth, think, great, safe, glad
  Topic 3: london, weather, safe, feel, return, thing, departur, forecast, case, standbi
  Topic 4: voucher, sir, apolog, miss, tomorrow, guess, refund, provid, sorri, connect

Call Reason: Communications
  Topic 1: voucher, sir, apolog, miss, refund, guess, tomorrow, provid, sorri, experi
  Topic 2: 150, monday, return, great, friday, differ, waiv, tuesday, thursday, saturday
  Topic 3: upgrad, economi, tri, standbi, class, open, bag, list, th

In [188]:
# # Display the topics for each reason
# for reason, topics in topic_keywords_uncleaned.items():
#     print(f"\nCall Reason: {reason}")
#     for idx, topic in enumerate(topics):
#         print(f"  Topic {idx + 1}: {', '.join(topic)}")


In [196]:
# Display the first few rows of a specific reason DataFrame to show the dominant topics
reason = 'Products and Services'  # Example
print(split_dataframes[reason][['call_transcript', 'dominant_topic']])

                                         call_transcript  dominant_topic
12     phone dial ugh final someon answer hold forev ...               0
35     hello speak jame jame upcom york san francisco...               1
37     john suppos 2pm email say 1pm ua45212 sigh res...               1
86     john complain recent york whole experi nightma...               0
93     michael took york san francisco 3 miss import ...               0
100    kelli san francisco tomorrow 4 ridicul sigh so...               1
130    david final took long someon pick phone wait s...               0
133    sarah suppos tomorrow sorri hear happen due se...               1
172    jack assist sigh angrili london month log acco...               0
192    sam sam ah shoot paper rustl san francisco tue...               2
210    cust hello suppos morn afternoon john cust san...               0
231    john suppos morn gon na miss connect unaccept ...               0
242    john sigh nightmar sorri hear provid rustl p

In [140]:
split_dataframes['Baggage']

Unnamed: 0     call_id  customer_id  agent_id  \
60             60   687556900   9348058886    391212   
79             79  2835524012   8798729337    600666   
83             83  4350015240   6223747949    215457   
128           128  4075573598   4405753886    436472   
167           167  1589048482   1536516864    696673   
182           182  7929224394   9455428741    645129   
202           202   607499611   5506632838    309976   
260           260  4220851729   1691252590    519294   
270           270  6612130758    970082846    633922   
309           309  2444517954   5174097533    519057   
340           340  4729597079   9736899948    289402   
347           347  5388689631   4625465517    499403   
364           364  8124325105   2429674930    915618   
379           379  4375012633   9792328141    607742   
391           391  4277990670   7575796105    192245   
469           469  8758022901    315297318    931734   
483           483  1239178323   1701184242    645129   
499           499  4573130208    905195962    542034   
502           502  4281700298   2044675560    965878   
528           528  4250721052   9320592198    715813   
568           568  5801430084   9668744594    422969   
571           571  8030169881   2580224488    901589   
578           578  5207967963   1939951086    792482   
598           598  9672752882   6097302814    641379   
644           644  4016778662   4042324340    519057   
723           723   110113510   8605096431    882260   
745           745  8449789488   2394824873    957331   
753           753  8906333582   7247327958    825827   
789           789  8435733051   9534303221    819946   
826           826  9324149936   3725374566    357288   
843           843  2619494591   9875142088    901589   
908           908  3252390779   9753277601    308266   
976           976  1105478868   2550117133    600666   
977           977  5125515589   6294268928    641379   
982           982  9803893687   3578822810    342345   
985           985  6233719494   9668203131    901589   
988           988  3846877410   8817492815    349957   
1014         1014   581733221   2708842074    937806   
1064         1064  7083451765   1140478121    388661   
1118         1118  4839007811   5477061252    470164   
1122         1122  5418752623   8829648525    630891   
1149         1149  4634216240   1388165184    204674   
1183         1183    28698213   3150258310    519294   
1187         1187  1304160316   2792917143    422969   
1215         1215  5430596771      1013433    633922   
1244         1244  6398926000   3316739245    633922   
1247         1247   478367604   8550859564    720418   
1248         1248  8122877877   1382383511    233571   
1269         1269  8388685903   8363166981    633922   
1295         1295  1652730655   7234197530    980508   
1343         1343  4675010716   2356514832    814752   
1351         1351  1618078339   1845574960    605855   
1384         1384   831792537   2270369082    618490   
1395         1395  9420681418   3438882447    261911   
1473         1473    94764405    710616642    642658   
1493         1493  7178923409    279434302    901722   
1544         1544  7568913259   3618532018    981779   
1554         1554  3979638553   3286782574    672758   
1560         1560   521608355   3034178828    591324   
1628         1628  7057028309   6555742115    265196   
1664         1664  5736769362   9187250303    764745   
1671         1671  7559715803   9913332538    437196   
1686         1686  4957097109   8181684691    552900   
1726         1726  6475788031   6238467422    271366   
1727         1727  9874293621   4231935471    786323   
1767         1767  6483553246    822718122    374078   
1773         1773  4615824059    496051085    176703   
1805         1805  5152260601   8753612971    769083   
1806         1806  1865141600   6685588120    915618   
1821         1821  1356740595   4345509452    524049   
1925         1925  3252012735  

In [131]:
df.head()

Unnamed: 0     call_id  customer_id  agent_id  call_start_datetime  \
4712        4712  8326955206   4706903050    595713  2024-08-03 13:15:00   
4725        4725  3218394191   8424797559    630891  2024-08-03 13:18:00   
4762        4762  1349952018   4822049335    981779  2024-08-03 13:23:00   
4766        4766  4320026620   8873327345    642658  2024-08-03 13:24:00   
4788        4788   793280037   3878408890    437196  2024-08-03 13:26:00   

     agent_assigned_datetime    call_end_datetime  \
4712     2024-08-03 13:20:00  2024-08-03 13:21:00   
4725     2024-08-03 13:22:00  2024-08-03 13:35:00   
4762     2024-08-03 13:28:00  2024-08-03 13:38:00   
4766     2024-08-03 13:29:00  2024-08-03 14:15:00   
4788     2024-08-03 13:31:00  2024-08-03 13:32:00   

                                        call_transcript  Handle_time  \
4712  \n\nAgent: Thank you for calling United Airlin...          1.0   
4725  \n\nAgent: Thank you for calling United Airlin...         13.0   
4762  \n\nAgent: Thank you for calling United Airlin...         10.0   
4766  \n\nAgent: Thank you for calling United Airlin...         46.0   
4788  \n\nAgent: Thank you for calling United Airlin...          1.0   

      Wait_time    primary_call_reason  hour  \
4712        5.0  Products and Services    13   
4725        4.0  Products and Services    13   
4762        5.0  Products and Services    13   
4766        5.0  Products and Services    13   
4788        5.0  Products and Services    13   

                                     topic_distribution  dominant_topic  
4712  [0.27992571371305275, 0.37070599687624467, 0.3...               1  
4725  [0.023574212775492983, 0.0016826199145946533, ...               2  
4762  [0.0012422985117737815, 0.9961851660397325, 0....               1  
4766  [0.0014983535194287344, 0.0015061871022569444,...               2  
4788  [0.002148028879356053, 0.13649338367109723, 0....               3

In [195]:

for reason, topics in topic_keywords.items():
    # Create an empty list to store the topics with their keywords as strings
    topic_descriptions = []
    
    # Iterate over each topic and create a string with the topic index and its keywords
    for idx, topic in enumerate(topics):
        topic_str = f"Topic {idx + 1}: {', '.join(topic)}"
        topic_descriptions.append(topic_str)
    
    # Convert the list of topic descriptions into a single string (for storing in the DataFrame)
    all_topics_str = "\n".join(topic_descriptions)
    
    # Check if the reason exists in split_dataframes
    if reason in split_dataframes:
        # Add a new column 'topic_keywords' to store the topics in the DataFrame for that reason
        split_dataframes[reason]['topic_keywords'] = all_topics_str
    
    # Optional: You can print or inspect the DataFrame to verify
    print(f"\nStored topics for reason: {reason}")
    print(split_dataframes[reason].head())  # Display first few rows to verify



Stored topics for reason: Post Flight
    Unnamed: 0     call_id  customer_id  agent_id  \
0            0  3817230689    390235425    922729   
1            1  4886165173   9360139623    964561   
24          24  5401438897   6942343286    274746   
34          34  6062040810   4689597701    131036   
36          36   949356313   6440512032    215457   

                                      call_transcript  call_start_datetime  \
0   clair clair seattl thursday johnson ua1572 10a...  2024-08-01 05:03:00   
1   steve suppos 3 miss connect sorri hear never f...  2024-08-01 05:26:00   
24  rachel rachel come 4532 denver tuesday questio...  2024-08-01 09:00:00   
34  anna speak anna upcom york lo angel found retu...  2024-08-01 09:13:00   
36  dave denver suppos yesterday miss connect sorr...  2024-08-01 09:20:00   

   agent_assigned_datetime    call_end_datetime primary_call_reason  \
0      2024-08-01 05:12:00  2024-08-01 05:25:00         Post Flight   
1      2024-08-01 05:36:00  202

In [194]:
split_dataframes['Seating']['dominant_topic'].value_counts()

0    2890
3    2238
2     646
1     591
Name: dominant_topic, dtype: int64

In [197]:
split_dataframes['Post Flight']

Unnamed: 0     call_id  customer_id  agent_id  \
0               0  3817230689    390235425    922729   
1               1  4886165173   9360139623    964561   
24             24  5401438897   6942343286    274746   
34             34  6062040810   4689597701    131036   
36             36   949356313   6440512032    215457   
52             52  2306900525   8636556192    153460   
62             62  3789748403   3646033723    153460   
76             76  7161945208   5030908011    825827   
84             84    73275311   3654551536    825827   
87             87  3709853620   8015461432    462743   
97             97  6175469461     50419257    663804   
102           102  3126882058   7479180549    591324   
111           111  5844224803   2771225033    663804   
122           122  5859728512   1726454999    645129   
141           141  5549013191   7430747231    594957   
178           178  6606952927   2452419342    784648   
180           180  2600260910   6096933398    782403   
184           184  5614887597   1501813477    171021   
224           224  3067054150   6153880444    149315   
248           248  8144603704   7574512415    901589   
267           267  7833312599   7134676956    213093   
280           280  2447978634   1424540144    305039   
286           286  6119975393   6704905640    544771   
304           304  9003249557   3438100250    964561   
308           308   976916902   1458170297    274746   
331           331  2555815221   2442986542    922729   
339           339  7375608133   9099699951    215457   
367           367  7946995905   3997414865    131036   
375           375  3670759426   1821540333    524049   
393           393  5610113427   6237260979    814752   
397           397  9397309729   6581041779    462743   
410           410  6917164168   1259079781    289402   
413           413  6031599224   4616080717    814752   
420           420  2998096258    172992063    369972   
439           439  9759668685   4835939396    153460   
440           440  7574895296   3888549464    376343   
444           444  4416852233   2867549678    542034   
449           449   928150810   8054361516    462743   
466           466  3685534705   2197745882    349957   
467           467  8562829114   8941602103    391212   
470           470  4842708127    254618547    696673   
485           485  2971133759   7628816175    782403   
505           505   485086782   5762727862    852493   
527           527  8581437415   1997722543    126555   
530           530  6945022550   6508204109    347606   
545           545  7916581442   4402057363    149315   
570           570  3643813726   8804484597    537208   
586           586  3617137159   7599671640    126555   
596           596  8221536415   3346055606    731717   
604           604  8096134775   3701962521    910145   
610           610  1636606919    382234023    250675   
632           632    51035785   6709864479    436160   
654           654  9739635653   6970484692    131036   
655           655  6386902668   9314894226    519057   
669           669  7798200086   6125200961    964561   
687           687  7575318256   3495603097    878048   
688           688  8923227201   6155461078    289402   
691           691  7648813153   1322435618    825827   
694           694  8636691184   8555398988    274746   
698           698  2031196828   8062388311    915618   
702           702  9294844442   3076123881    663804   
747           747  6958732590   7358128276    499403   
758           758   473879884   6414957308    619806   
793           793  8730054794   9821625526    619806   
820           820  6868468799     99031999    342345   
835           835  4530039805   6861736759    418648   
850           850  5804992339   6743995863    192245   
853           853  4788660164    726090243    391212   
855           855    86515681   4790427985    882260   
862           862  8028642102   9945015547    880532   
869           869  2504070888  

In [198]:
for reason,df in split_dataframes.items():
    split_dataframes[reason].to_csv(f"{reason}.csv")

In [201]:
import pandas as pd

# The new data as a dictionary
new_topic_keywords = {
    "Post Flight": [
        ["voucher", "weather", "experi", "provid", "miss", "bag", "refund", "compens", "apolog", "happen"],
        ["tomorrow", "sir", "apolog", "ugh", "connect", "guess", "inconveni", "suppos", "sigh", "york"],
        ["credit", "refund", "ticket", "abl", "use", "offer", "200", "someth", "feel", "pay"],
        ["great", "monday", "return", "tuesday", "thursday", "friday", "email", "150", "enjoy", "safe"]
    ],
    "Seating": [
        ["150", "monday", "great", "friday", "differ", "waiv", "tuesday", "john", "thursday", "saturday"],
        ["upgrad", "bag", "doubl", "question", "economi", "everyth", "think", "great", "safe", "glad"],
        ["london", "weather", "safe", "feel", "return", "thing", "departur", "forecast", "case", "standbi"],
        ["voucher", "sir", "apolog", "miss", "tomorrow", "guess", "refund", "provid", "sorri", "connect"]
    ],
    "Communications": [
        ["voucher", "sir", "apolog", "miss", "refund", "guess", "tomorrow", "provid", "sorri", "experi"],
        ["150", "monday", "return", "great", "friday", "differ", "waiv", "tuesday", "thursday", "saturday"],
        ["upgrad", "economi", "tri", "standbi", "class", "open", "bag", "list", "think", "question"],
        ["weather", "connect", "denver", "safe", "london", "arriv", "depart", "feel", "forecast", "san"]
    ],
    "Traveler Updates": [
        ["monday", "tuesday", "150", "waiv", "sam", "pay", "75", "john", "smith", "someth"],
        ["san", "francisco", "return", "great", "think", "safe", "question", "john", "enjoy", "depart"],
        ["sir", "apolog", "voucher", "miss", "guess", "refund", "connect", "provid", "tomorrow", "sorri"],
        ["friday", "differ", "saturday", "thursday", "great", "pay", "hmm", "ticket", "goodby", "150"]
    ],
    "Upgrade": [
        ["150", "monday", "return", "waiv", "differ", "tuesday", "pay", "great", "hmm", "friday"],
        ["voucher", "refund", "experi", "provid", "compens", "miss", "apolog", "sir", "offer", "sorri"],
        ["tomorrow", "connect", "ugh", "sir", "guess", "denver", "apolog", "inconveni", "san", "suppos"],
        ["great", "question", "safe", "departur", "think", "email", "depart", "convers", "glad", "enjoy"]
    ],
    "IRROPS": [
        ["weather", "london", "feel", "question", "safe", "upgrad", "think", "bag", "depart", "great"],
        ["tomorrow", "connect", "sir", "ugh", "guess", "apolog", "inconveni", "york", "miss", "sigh"],
        ["monday", "150", "friday", "great", "tuesday", "differ", "thursday", "saturday", "john", "smith"],
        ["refund", "voucher", "experi", "miss", "compens", "provid", "offer", "apolog", "sir", "500"]
    ],
    "Products and Services": [
        ["sir", "voucher", "refund", "apolog", "guess", "miss", "provid", "sorri", "inconveni", "compens"],
        ["tomorrow", "connect", "denver", "weather", "safe", "arriv", "morn", "depart", "ugh", "email"],
        ["monday", "return", "great", "150", "thursday", "tuesday", "friday", "email", "waiv", "differ"],
        ["upgrad", "bag", "credit", "economi", "think", "thing", "ticket", "question", "london", "class"]
    ],
    "Mileage Plus": [
        ["refund", "voucher", "experi", "miss", "provid", "offer", "compens", "apolog", "sir", "sorri"],
        ["question", "weather", "london", "safe", "departur", "feel", "think", "great", "depart", "doubl"],
        ["tomorrow", "connect", "sir", "ugh", "guess", "miss", "apolog", "inconveni", "sigh", "denver"],
        ["return", "150", "monday", "great", "friday", "thursday", "pay", "tuesday", "waiv", "differ"]
    ],
    "Voluntary Change": [
        ["150", "waiv", "monday", "differ", "pay", "credit", "return", "ticket", "friday", "abl"],
        ["upgrad", "connect", "denver", "tomorrow", "ugh", "tri", "arriv", "economi", "open", "minut"],
        ["voucher", "sir", "apolog", "miss", "refund", "provid", "guess", "sorri", "weather", "experi"],
        ["great", "friday", "depart", "enjoy", "email", "san", "return", "safe", "francisco", "question"]
    ],
    "Booking": [
        ["monday", "return", "150", "friday", "tuesday", "great", "differ", "thursday", "hmm", "pay"],
        ["tomorrow", "connect", "sir", "ugh", "guess", "apolog", "denver", "inconveni", "miss", "sigh"],
        ["voucher", "refund", "experi", "provid", "miss", "sir", "compens", "apolog", "offer", "sorri"],
        ["question", "weather", "london", "safe", "depart", "great", "feel", "think", "doubl", "glad"]
    ],
    "Digital Support": [
        ["150", "monday", "friday", "return", "differ", "tuesday", "great", "pay", "email", "hmm"],
        ["refund", "credit", "voucher", "provid", "experi", "offer", "compens", "sir", "futur", "miss"],
        ["connect", "tomorrow", "miss", "apolog", "sir", "guess", "voucher", "ugh", "inconveni", "suppos"],
        ["san", "francisco", "question", "upgrad", "safe", "weather", "departur", "think", "doubl", "feel"]
    ],
    "Disability": [
        ["refund", "voucher", "credit", "provid", "experi", "futur", "compens", "weather", "miss", "offer"],
        ["upgrad", "bag", "class", "apolog", "economi", "guess", "sir", "caus", "busi", "mile"],
        ["connect", "miss", "tomorrow", "denver", "ugh", "guess", "sir", "apolog", "rebook", "suppos"],
        ["great", "thursday", "return", "friday", "150", "tuesday", "safe", "question", "think", "departur"]
    ],
    "Voluntary Cancel": [
        ["voucher", "sir", "apolog", "refund", "miss", "guess", "sorri", "provid", "tomorrow", "inconveni"],
        ["connect", "weather", "san", "francisco", "safe", "arriv", "standbi", "forecast", "denver", "case"],
        ["great", "upgrad", "saturday", "return", "convers", "london", "natur", "tone", "come", "think"],
        ["150", "monday", "waiv", "differ", "pay", "san", "francisco", "friday", "tuesday", "credit"]
    ],
    "Baggage": [
        ["150", "friday", "return", "great", "monday", "tuesday", "differ", "waiv", "pay", "thursday"],
        ["tomorrow", "connect", "sir", "ugh", "guess", "apolog", "inconveni", "sigh", "miss", "denver"],
        ["question", "weather", "feel", "london", "safe", "doubl", "thing", "depart", "think", "departur"],
        ["voucher", "refund", "experi", "miss", "provid", "offer", "compens", "apolog", "bag", "weather"]
    ],
    "ETC": [
        ["tomorrow", "connect", "denver", "miss", "apolog", "sir", "guess", "ugh", "sorri", "inconveni"],
        ["refund", "voucher", "sir", "provid", "experi", "apolog", "weather", "miss", "guess", "compens"],
        ["san", "francisco", "great", "tuesday", "question", "thursday", "safe", "departur", "glad", "think"],
        ["friday", "return", "150", "monday", "differ", "waiv", "pay", "credit", "hmm", "someth"]
    ],
    "Other Topics": [
        ["weather", "question", "departur", "safe", "bag", "feel", "london", "glad", "think", "doubl"],
        ["tomorrow", "connect", "miss", "sir", "ugh", "apolog", "guess", "inconveni", "denver", "suppos"],
        ["refund", "experi", "voucher", "sorri", "compens", "apolog", "offer", "provid", "miss", "credit"],
        ["return", "great", "friday", "monday", "150", "differ", "hmm", "tuesday", "john", "saturday"]
    ],
    "Check In": [
        ["san", "francisco", "safe", "question", "feel", "thing", "great", "weather", "come", "glad"],
        ["experi", "bag", "refund", "voucher", "provid", "offer", "apolog", "sorri", "compens", "happen"],
        ["150", "return", "friday", "monday", "differ", "great", "pay", "hmm", "waiv", "tuesday"],
        ["miss", "tomorrow", "sir", "connect", "apolog", "voucher", "guess", "ugh", "inconveni", "sorri"]
    ],
    "Schedule Change": [
        ["tomorrow", "connect", "sir", "ugh", "guess", "york", "miss", "apolog", "inconveni", "denver"],
        ["refund", "voucher", "experi", "provid", "compens", "miss", "offer", "500", "apolog", "sorri"],
        ["150", "monday", "friday", "great", "thursday", "tuesday", "john", "return", "hmm", "differ"],
        ["weather", "upgrad", "question", "bag", "safe", "mind", "doubl", "feel", "think", "forecast"]
    ],
    "Checkout": [
        ["credit", "refund", "offer", "ticket", "futur", "abl", "minut", "provid", "use", "sir"],
        ["great", "150", "monday", "return", "thursday", "tuesday", "friday", "email", "enjoy", "think"],
        ["weather", "voucher", "miss", "experi", "provid", "bag", "compens", "caus", "apolog", "sir"],
        ["tomorrow", "connect", "ugh", "denver", "guess", "york", "upgrad", "sir", "inconveni", "apolog"]
    ],
    "Unaccompanied Minor": [
        ["return", "monday", "saturday", "email", "john", "london", "tri", "friday", "york", "tomorrow"],
        ["sam", "150", "great", "paus", "departur", "glad", "standbi", "hmm", "thursday", "abl"],
        ["voucher", "miss", "apolog", "sir", "refund", "guess", "provid", "compens", "bag", "sorri"],
        ["san", "francisco", "tuesday", "great", "question", "pay", "smith", "depart", "enjoy", "bye"]
    ]
}

# Preparing the DataFrame
rows = []
for call_reason, topics in new_topic_keywords.items():
    for i, keywords in enumerate(topics, start=1):
        rows.append([call_reason, f"{i-1}", ", ".join(keywords)])

# Creating DataFrame
df = pd.DataFrame(rows, columns=["Call Reason", "Topic", "Keywords"])

# Display DataFrame
df


Call Reason Topic  \
0             Post Flight     0   
1             Post Flight     1   
2             Post Flight     2   
3             Post Flight     3   
4                 Seating     0   
5                 Seating     1   
6                 Seating     2   
7                 Seating     3   
8          Communications     0   
9          Communications     1   
10         Communications     2   
11         Communications     3   
12       Traveler Updates     0   
13       Traveler Updates     1   
14       Traveler Updates     2   
15       Traveler Updates     3   
16                Upgrade     0   
17                Upgrade     1   
18                Upgrade     2   
19                Upgrade     3   
20                 IRROPS     0   
21                 IRROPS     1   
22                 IRROPS     2   
23                 IRROPS     3   
24  Products and Services     0   
25  Products and Services     1   
26  Products and Services     2   
27  Products and Services     3   
28           Mileage Plus     0   
29           Mileage Plus     1   
30           Mileage Plus     2   
31           Mileage Plus     3   
32       Voluntary Change     0   
33       Voluntary Change     1   
34       Voluntary Change     2   
35       Voluntary Change     3   
36                Booking     0   
37                Booking     1   
38                Booking     2   
39                Booking     3   
40        Digital Support     0   
41        Digital Support     1   
42        Digital Support     2   
43        Digital Support     3   
44             Disability     0   
45             Disability     1   
46             Disability     2   
47             Disability     3   
48       Voluntary Cancel     0   
49       Voluntary Cancel     1   
50       Voluntary Cancel     2   
51       Voluntary Cancel     3   
52                Baggage     0   
53                Baggage     1   
54                Baggage     2   
55                Baggage     3   
56                    ETC     0   
57                    ETC     1   
58                    ETC     2   
59                    ETC     3   
60           Other Topics     0   
61           Other Topics     1   
62           Other Topics     2   
63           Other Topics     3   
64               Check In     0   
65               Check In     1   
66               Check In     2   
67               Check In     3   
68        Schedule Change     0   
69        Schedule Change     1   
70        Schedule Change     2   
71        Schedule Change     3   
72               Checkout     0   
73               Checkout     1   
74               Checkout     2   
75               Checkout     3   
76    Unaccompanied Minor     0   
77    Unaccompanied Minor     1   
78    Unaccompanied Minor     2   
79    Unaccompanied Minor     3   

                                             Keywords  
0   voucher, weather, experi, provid, miss, bag, r...  
1   tomorrow, sir, apolog, ugh, connect, guess, in...  
2   credit, refund, ticket, abl, use, offer, 200, ...  
3   great, monday, return, tuesday, thursday, frid...  
4   150, monday, great, friday, differ, waiv, tues...  
5   upgrad, bag, doubl, question, economi, everyth...  
6   london, weather, safe, feel, return, thing, de...  
7   voucher, sir, apolog, miss, tomorrow, guess, r...  
8   voucher, sir, apolog, miss, refund, guess, tom...  
9   150, monday, return, great, friday, differ, wa...  
10  upgrad, economi, tri, standbi, class, open, ba...  
11  weather, connect, denver, safe, london, arriv,...  
12  monday, tuesday, 150, waiv, sam, pay, 75, john...  
13  san, francisco, return, great, think, safe, qu...  
14  sir, apolog, voucher, miss, guess, refund, con...  
15  friday, differ, saturday, thursday, great, pay...  
16  150, monday, return, waiv, differ, tuesday, pa...  
17  voucher, refund, experi, provid, compens, miss...  
18  tomorrow, connect, ugh, sir, guess, denver, ap...  
19  great, question, safe, departur, think, email,...  
20

In [180]:
df.head()

Call Reason    Topic                                           Keywords
0  Post Flight  Topic 1  voucher, weather, experi, provid, miss, bag, r...
1  Post Flight  Topic 2  tomorrow, sir, apolog, ugh, connect, guess, in...
2  Post Flight  Topic 3  credit, refund, ticket, abl, use, offer, 200, ...
3  Post Flight  Topic 4  great, monday, return, tuesday, thursday, frid...
4      Seating  Topic 1  150, monday, great, friday, differ, waiv, tues...

In [202]:
df.to_csv('keywords.csv')

In [203]:
def predict_reason(transcript_tokens, reason_topics):
    scores = {}
    
    # Loop through each call reason's topic words
    for reason, topic_words in reason_topics.items():
        # Count the overlap between the transcript tokens and the topic words
        overlap_count = sum(1 for word in transcript_tokens if word in topic_words)
        scores[reason] = overlap_count
    
    # Find the call reason with the maximum overlap (highest score)
    predicted_reason = max(scores, key=scores.get)
    return predicted_reason, scoresdef predict_reason(transcript_tokens, reason_topics):
    scores = {}def predict_reason(transcript_tokens, reason_topics):
    scores = {}
    
    # Loop through each call reason's topic words
    for reason, topic_words in reason_topics.items():
        # Count the overlap between the transcript tokens and the topic words
        overlap_count = sum(1 for word in transcript_tokens if word in topic_words)
        scores[reason] = overlap_count
    
    # Find the call reason with the maximum overlap (highest score)
    predicted_reason = max(scores, key=scores.get)
    return predicted_reason, scores
    
    # Loop through each call reason's topic words
    for reason, topic_words in reason_topics.items():
        # Count the overlap between the transcript tokens and the topic words
        overlap_count = sum(1 for word in transcript_tokens if word in topic_words)
        scores[reason] = overlap_count
    
    # Find the call reason with the maximum overlap (highest score)
    predicted_reason = max(scores, key=scores.get)
    return predicted_reason, scores

SyntaxError: invalid syntax (Temp/ipykernel_21288/1563214781.py, line 12)